In [2]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))


def map_new_to_old_style(sequence):
    types = []
    landmark_indexes = []
    for column in list(sequence.columns)[1:544]:
        parts = column.split("_")
        if len(parts) == 4:
            types.append(parts[1] + "_" + parts[2])
        else:
            types.append(parts[1])

        landmark_indexes.append(int(parts[-1]))

    data = {
        "frame": [],
        "type": [],
        "landmark_index": [],
        "x": [],
        "y": [],
        "z": []
    }

    for index, row in sequence.iterrows():
        data["frame"] += [int(row.frame)]*543
        data["type"] += types
        data["landmark_index"] += landmark_indexes

        for _type, landmark_index in zip(types, landmark_indexes):
            data["x"].append(row[f"x_{_type}_{landmark_index}"])
            data["y"].append(row[f"y_{_type}_{landmark_index}"])
            data["z"].append(row[f"z_{_type}_{landmark_index}"])

    return pd.DataFrame.from_dict(data)

# assign desired colors to landmarks
def assign_color(row):
    if row == 'face':
        return 'red'
    elif 'hand' in row:
        return 'dodgerblue'
    else:
        return 'green'

# specifies the plotting order
def assign_order(row):
    if row.type == 'face':
        return row.landmark_index + 101
    elif row.type == 'pose':
        return row.landmark_index + 30
    elif row.type == 'left_hand':
        return row.landmark_index + 80
    else:
        return row.landmark_index
    
def visualise2d_landmarks(parquet_df, title=""):
    connections = [  
        [0, 1, 2, 3, 4,],
        [0, 5, 6, 7, 8],
        [0, 9, 10, 11, 12],
        [0, 13, 14, 15, 16],
        [0, 17, 18, 19, 20],

        
        [38, 36, 35, 34, 30, 31, 32, 33, 37],
        [40, 39],
        [52, 46, 50, 48, 46, 44, 42, 41, 43, 45, 47, 49, 45, 51],
        [42, 54, 56, 58, 60, 62, 58],
        [41, 53, 55, 57, 59, 61, 57],
        [54, 53],

        
        [80, 81, 82, 83, 84, ],
        [80, 85, 86, 87, 88],
        [80, 89, 90, 91, 92],
        [80, 93, 94, 95, 96],
        [80, 97, 98, 99, 100], ]

    parquet_df = map_new_to_old_style(parquet_df)
    frames = sorted(set(parquet_df.frame))
    first_frame = min(frames)
    parquet_df['color'] = parquet_df.type.apply(lambda row: assign_color(row))
    parquet_df['plot_order'] = parquet_df.apply(lambda row: assign_order(row), axis=1)
    first_frame_df = parquet_df[parquet_df.frame == first_frame].copy()
    first_frame_df = first_frame_df.sort_values(["plot_order"]).set_index('plot_order')


    frames_l = []
    for frame in frames:
        filtered_df = parquet_df[parquet_df.frame == frame].copy()
        filtered_df = filtered_df.sort_values(["plot_order"]).set_index("plot_order")
        traces = [go.Scatter(
            x=filtered_df['x'],
            y=filtered_df['y'],
            mode='markers',
            marker=dict(
                color=filtered_df.color,
                size=9))]

        for i, seg in enumerate(connections):
            trace = go.Scatter(
                    x=filtered_df.loc[seg]['x'],
                    y=filtered_df.loc[seg]['y'],
                    mode='lines',
            )
            traces.append(trace)
        frame_data = go.Frame(data=traces, traces = [i for i in range(17)])
        frames_l.append(frame_data)

    traces = [go.Scatter(
        x=first_frame_df['x'],
        y=first_frame_df['y'],
        mode='markers',
        marker=dict(
            color=first_frame_df.color,
            size=9
        )
    )]
    for i, seg in enumerate(connections):
        trace = go.Scatter(
            x=first_frame_df.loc[seg]['x'],
            y=first_frame_df.loc[seg]['y'],
            mode='lines',
            line=dict(
                color='black',
                width=2
            )
        )
        traces.append(trace)
    fig = go.Figure(
        data=traces,
        frames=frames_l
    )


    fig.update_layout(
        width=500,
        height=800,
        scene={
            'aspectmode': 'data',
        },
        updatemenus=[
            {
                "buttons": [
                    {
                        "args": [None, {"frame": {"duration": 300,
                                                  "redraw": True},
                                        "fromcurrent": True,
                                        "transition": {"duration": 0}}],
                        "label": "&#9654;",
                        "method": "animate",
                    },
                    {
                        "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                          "mode": "immediate",
                                          "transition": {"duration": 0}}],
                        "label": "&#9612;&#9612;",
                        "method": "animate",
                    },
                ],
                "direction": "left",
                "pad": {"r": 100, "t": 100},
                "font": {"size":20},
                "type": "buttons",
                "x": 0.1,
                "y": 0,
            }
        ],
    )
    camera = dict(
        up=dict(x=0, y=-1, z=0),
        eye=dict(x=0, y=0, z=2.5)
    )
    fig.update_layout(title_text=title, title_x=0.5)
    fig.update_layout(scene_camera=camera, showlegend=False)
    fig.update_layout(xaxis = dict(visible=False),
            yaxis = dict(visible=False),
    )
    fig.update_yaxes(autorange="reversed")

    fig.show()
    
def get_phrase(df, file_id, sequence_id):
    return df[
        np.logical_and(
            df.file_id == file_id, 
            df.sequence_id == sequence_id
        )
    ].phrase.iloc[0]

import pandas as pd,numpy as np,os
import json
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.io as pio
from pathlib import Path
pio.templates.default = "simple_white"
print("importing..")

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/asl-fingerspelling/supplemental_metadata.csv
/kaggle/input/asl-fingerspelling/character_to_prediction_index.json
/kaggle/input/asl-fingerspelling/train.csv
/kaggle/input/asl-fingerspelling/supplemental_landmarks/371169664.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/369584223.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/1682915129.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/775880548.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/2100073719.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/1650637630.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/1471096258.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/86446671.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/897287709.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/333606065.parquet
/kaggle/input/asl-fingerspelling/supplemental_landmarks/2057261717.parquet
/kaggle/inpu

In [3]:
data = pd.read_csv('/kaggle/input/frame-9-data/frame-9-data.csv')

In [4]:
left_data = data[(data['x_left_hand_10'] != 0) & (data['x_right_hand_10'] == 0)]

In [5]:
right_data = data[(data['x_right_hand_10'] != 0) & (data['x_left_hand_10'] == 0)]

In [152]:
left_data

sequence_id  frame  x_left_hand_0  x_left_hand_1  x_left_hand_2  \
12      1817221592    9.0       0.563295       0.459576       0.381724   
15      1817248431    9.0       0.680857       0.577381       0.505314   
17      1817348598    9.0       0.956424       0.889103       0.818419   
20      1817382273    9.0       0.802836       0.736705       0.673200   
25      1817651236    9.0       0.856107       0.756596       0.692620   
...            ...    ...            ...            ...            ...   
67233    386361726    9.0       0.598941       0.518246       0.480507   
67234    386466332    9.0       0.599616       0.537741       0.475229   
67267    387390786    9.0       0.585973       0.480971       0.346336   
67284    388225542    9.0       0.658460       0.576647       0.500126   
67285    388232076    9.0       0.832166       0.812121       0.697527   

       x_left_hand_3  x_left_hand_4  x_left_hand_5  x_left_hand_6  \
12          0.321069       0.285747       0.490891       0.451477   
15          0.478172       0.466133       0.570973       0.534812   
17          0.765783       0.722212       0.831799       0.755638   
20          0.646170       0.657284       0.702647       0.655930   
25          0.653095       0.628491       0.698044       0.625628   
...              ...            ...            ...            ...   
67233       0.499069       0.523064       0.554946       0.477944   
67234       0.435517       0.414458       0.547506       0.535840   
67267       0.270746       0.226656       0.408268       0.342510   
67284       0.436581       0.374855       0.554448       0.494012   
67285       0.569774       0.467846       0.735782       0.526173   

       x_left_hand_7  ...    r    s    t    u    v    w    x    y    z    ~  
12          0.401009  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
15          0.509518  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
17          0.716922  ...  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  
20          0.620662  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
25          0.603176  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
...              ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
67233       0.446889  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67234       0.498025  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67267       0.326518  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67284       0.447618  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67285       0.400693  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[6552 rows x 187 columns]

In [153]:
right_data

sequence_id  frame  x_left_hand_0  x_left_hand_1  x_left_hand_2  \
2       1816825349    9.0            0.0            0.0            0.0   
3       1816862427    9.0            0.0            0.0            0.0   
4       1816909464    9.0            0.0            0.0            0.0   
5       1816967051    9.0            0.0            0.0            0.0   
6       1817123330    9.0            0.0            0.0            0.0   
...            ...    ...            ...            ...            ...   
67278    387936100    9.0            0.0            0.0            0.0   
67279    387993269    9.0            0.0            0.0            0.0   
67280    387998966    9.0            0.0            0.0            0.0   
67281    388064441    9.0            0.0            0.0            0.0   
67282    388105954    9.0            0.0            0.0            0.0   

       x_left_hand_3  x_left_hand_4  x_left_hand_5  x_left_hand_6  \
2                0.0            0.0            0.0            0.0   
3                0.0            0.0            0.0            0.0   
4                0.0            0.0            0.0            0.0   
5                0.0            0.0            0.0            0.0   
6                0.0            0.0            0.0            0.0   
...              ...            ...            ...            ...   
67278            0.0            0.0            0.0            0.0   
67279            0.0            0.0            0.0            0.0   
67280            0.0            0.0            0.0            0.0   
67281            0.0            0.0            0.0            0.0   
67282            0.0            0.0            0.0            0.0   

       x_left_hand_7  ...    r    s    t    u    v    w    x    y    z    ~  
2                0.0  ...  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
3                0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
4                0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
5                0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
6                0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
...              ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
67278            0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67279            0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67280            0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67281            0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67282            0.0  ...  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  

[32026 rows x 187 columns]

In [124]:
left_data[left_data['sequence_id'] == left_data.iat[450,0]]

sequence_id  frame  x_left_hand_0  x_left_hand_1  x_left_hand_2  \
4443   1099211857    9.0       0.718002       0.654294       0.593373   

      x_left_hand_3  x_left_hand_4  x_left_hand_5  x_left_hand_6  \
4443       0.555059       0.551153       0.595762       0.560208   

      x_left_hand_7  ...    r    s    t    u    v    w    x    y    z    ~  
4443        0.53032  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[1 rows x 187 columns]

In [6]:
train_df = pd.read_csv("/kaggle/input/asl-fingerspelling/train.csv")

In [125]:
train_df[train_df.sequence_id == 1099211857]

path    file_id  sequence_id  \
4442  train_landmarks/152029243.parquet  152029243   1099211857   

      participant_id            phrase  
4442             230  8572 ventura svc

In [8]:
sequence_id = 1099211857
file_id = 152029243

In [9]:
path_to_sign = f"/kaggle/input/asl-fingerspelling/train_landmarks/{file_id}.parquet"
sign = pd.read_parquet(path_to_sign)

In [10]:
sequence = sign[sign.index == sequence_id]

In [129]:
sequence['x_left_hand_0']

sequence_id
1099211857    0.931663
1099211857    0.881331
1099211857    0.847917
1099211857    0.819991
1099211857    0.795833
                ...   
1099211857    0.797012
1099211857    0.802488
1099211857    0.793164
1099211857    0.842518
1099211857    0.780154
Name: x_left_hand_0, Length: 166, dtype: float32

In [130]:
sequence_phrase = get_phrase(train_df, file_id, sequence_id)
visualise2d_landmarks(sequence, f"Phrase: {sequence_phrase}")

In [131]:
sequence

frame  x_face_0  x_face_1  x_face_2  x_face_3  x_face_4  \
sequence_id                                                            
1099211857       0  0.419562  0.421645  0.419796  0.408855  0.421332   
1099211857       1  0.417393  0.422326  0.419997  0.408732  0.422022   
1099211857       2  0.414767  0.416617  0.414784  0.403956  0.416468   
1099211857       3  0.410587  0.415554  0.413025  0.402119  0.415375   
1099211857       4  0.403763  0.410253  0.407732  0.397261  0.410131   
...            ...       ...       ...       ...       ...       ...   
1099211857     161  0.410336  0.419923  0.417038  0.408706  0.420468   
1099211857     162  0.416214  0.421062  0.418869  0.409434  0.421245   
1099211857     163  0.421309  0.428767  0.425986  0.416393  0.428914   
1099211857     164  0.426077  0.430404  0.428905  0.417189  0.429952   
1099211857     165  0.429053  0.433845  0.432891  0.420264  0.433194   

             x_face_5  x_face_6  x_face_7  x_face_8  ...  z_right_hand_11  \
sequence_id                                          ...                    
1099211857   0.420061  0.416054  0.326232  0.413934  ...              NaN   
1099211857   0.420489  0.415553  0.325498  0.413046  ...              NaN   
1099211857   0.415358  0.411678  0.322693  0.409715  ...              NaN   
1099211857   0.413958  0.409390  0.318050  0.407224  ...              NaN   
1099211857   0.408808  0.404408  0.314637  0.402239  ...              NaN   
...               ...       ...       ...       ...  ...              ...   
1099211857   0.419978  0.417637  0.326535  0.417148  ...              NaN   
1099211857   0.420536  0.417938  0.329128  0.417023  ...              NaN   
1099211857   0.427899  0.424277  0.334333  0.422857  ...              NaN   
1099211857   0.428573  0.424200  0.335969  0.421706  ...              NaN   
1099211857   0.431728  0.427656  0.337568  0.425246  ...              NaN   

             z_right_hand_12  z_right_hand_13  z_right_hand_14  \
sequence_id                                                      
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
...                      ...              ...              ...   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   

             z_right_hand_15  z_right_hand_16  z_right_hand_17  \
sequence_id                                                      
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
...                      ...              ...              ...   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   

             z_right_hand_18  z_right_hand_19  z_right_hand_20  
sequence_id                                                     
1099211857               NaN              NaN              NaN  
1099211857               NaN              NaN              NaN  
1099211857               NaN              NaN              NaN  
1099211857               NaN   

In [11]:
x_left_hand_cols = sequence.columns[np.arange(469,490)]
x_right_hand_cols = sequence.columns[np.arange(523,544)]

In [133]:
sequence[x_left_hand_cols]

x_left_hand_0  x_left_hand_1  x_left_hand_2  x_left_hand_3  \
sequence_id                                                               
1099211857        0.931663       0.852381       0.774159       0.714853   
1099211857        0.881331       0.806602       0.740600       0.695724   
1099211857        0.847917       0.772015       0.708921       0.660592   
1099211857        0.819991       0.751649       0.698077       0.662622   
1099211857        0.795833       0.726842       0.672116       0.640644   
...                    ...            ...            ...            ...   
1099211857        0.797012       0.704822       0.628558       0.562568   
1099211857        0.802488       0.715069       0.634076       0.568420   
1099211857        0.793164       0.717007       0.642982       0.579798   
1099211857        0.842518       0.721073       0.645008       0.576679   
1099211857        0.780154       0.701743       0.629699       0.569332   

             x_left_hand_4  x_left_hand_5  x_left_hand_6  x_left_hand_7  \
sequence_id                                                               
1099211857        0.674810       0.782371       0.734097       0.707111   
1099211857        0.690824       0.737288       0.690320       0.662282   
1099211857        0.616565       0.700687       0.652784       0.625782   
1099211857        0.634314       0.675149       0.626497       0.595596   
1099211857        0.621170       0.656568       0.607786       0.575676   
...                    ...            ...            ...            ...   
1099211857        0.508813       0.743832       0.625178       0.543188   
1099211857        0.517267       0.743279       0.626372       0.545939   
1099211857        0.523008       0.746383       0.632664       0.550494   
1099211857        0.519146       0.752389       0.640553       0.561313   
1099211857        0.512602       0.722402       0.622729       0.551570   

             x_left_hand_8  x_left_hand_9  ...  x_left_hand_11  \
sequence_id                                ...                   
1099211857        0.682476       0.830137  ...        0.755947   
1099211857        0.639733       0.787594  ...        0.733132   
1099211857        0.600735       0.749292  ...        0.695045   
1099211857        0.570600       0.721524  ...        0.665996   
1099211857        0.550304       0.699022  ...        0.642332   
...                    ...            ...  ...             ...   
1099211857        0.478079       0.753269  ...        0.523942   
1099211857        0.482254       0.751766  ...        0.520116   
1099211857        0.483576       0.756999  ...        0.532837   
1099211857        0.493868       0.768233  ...        0.543135   
1099211857        0.495892       0.734325  ...        0.538510   

             x_left_hand_12  x_left_hand_13  x_left_hand_14  x_left_hand_15  \
sequence_id                                                                   
1099211857         0.734033        0.884889        0.870147        0.858735   
1099211857         0.710516        0.841990        0.828090        0.814888   
1099211857         0.669353        0.802383        0.788673        0.772893   
1099211857         0.643233        0.772821        0.753769        0.737194   
1099211857         0.620995        0.748018        0.728475        0.711133   
...                     ...             ...             ...             ...   
1099211857         0.453221        0.744110        0.619709        0.530557   
1099211857         0.452850        0.744356        0.621002        0.530441   
1099211857         0.463666        0.751905        0.629155        0.540748   
1099211857         0.479261        0.767457        0.647695        0.560265   
1099211857         0.473502        0.735631        0.627250        0.546968   

             x_left_hand_16  x_left_hand_17  x_left_hand_18  x_left_hand_19  \
sequence_id                                                                   
1099211857      

In [135]:
sequence[x_right_hand_cols]

x_right_hand_0  x_right_hand_1  x_right_hand_2  x_right_hand_3  \
sequence_id                                                                   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
...                     ...             ...             ...             ...   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   

             x_right_hand_4  x_right_hand_5  x_right_hand_6  x_right_hand_7  \
sequence_id                                                                   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
...                     ...             ...             ...             ...   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   
1099211857              NaN             NaN             NaN             NaN   

             x_right_hand_8  x_right_hand_9  ...  x_right_hand_11  \
sequence_id                                  ...                    
1099211857              NaN             NaN  ...              NaN   
1099211857              NaN             NaN  ...              NaN   
1099211857              NaN             NaN  ...              NaN   
1099211857              NaN             NaN  ...              NaN   
1099211857              NaN             NaN  ...              NaN   
...                     ...             ...  ...              ...   
1099211857              NaN             NaN  ...              NaN   
1099211857              NaN             NaN  ...              NaN   
1099211857              NaN             NaN  ...              NaN   
1099211857              NaN             NaN  ...              NaN   
1099211857              NaN             NaN  ...              NaN   

             x_right_hand_12  x_right_hand_13  x_right_hand_14  \
sequence_id                                                      
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
...                      ...              ...              ...   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   
1099211857               NaN              NaN              NaN   

             x_right_hand_15  x_right_hand_16  x_right_hand_17  \
sequence_id                                                      
1099211857               NaN              NaN              NaN   
10

In [137]:
reversed_sequence = sequence

In [168]:
for i in range(21):
    reversed_sequence['x_right_hand_'+str(i)] = (0.0 - sequence['x_left_hand_'+str(i)]) + sequence['x_left_hand_0']
    reversed_sequence['y_right_hand_'+str(i)] = sequence['y_left_hand_'+str(i)]- sequence['y_left_hand_0']
    reversed_sequence['z_right_hand_'+str(i)] = sequence['z_left_hand_'+str(i)]- sequence['z_left_hand_0']

/tmp/ipykernel_28/68775810.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_28/68775810.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_28/68775810.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [170]:
reversed_sequence[x_right_hand_cols]

x_right_hand_0  x_right_hand_1  x_right_hand_2  x_right_hand_3  \
sequence_id                                                                   
1099211857              0.0        0.079282        0.157505        0.216810   
1099211857              0.0        0.074728        0.140730        0.185607   
1099211857              0.0        0.075903        0.138996        0.187325   
1099211857              0.0        0.068342        0.121914        0.157369   
1099211857              0.0        0.068991        0.123716        0.155188   
...                     ...             ...             ...             ...   
1099211857              0.0        0.092190        0.168454        0.234444   
1099211857              0.0        0.087419        0.168411        0.234068   
1099211857              0.0        0.076156        0.150182        0.213366   
1099211857              0.0        0.121445        0.197510        0.265839   
1099211857              0.0        0.078410        0.150455        0.210822   

             x_right_hand_4  x_right_hand_5  x_right_hand_6  x_right_hand_7  \
sequence_id                                                                   
1099211857         0.256853        0.149292        0.197566        0.224553   
1099211857         0.190507        0.144043        0.191011        0.219049   
1099211857         0.231353        0.147230        0.195134        0.222135   
1099211857         0.185677        0.144842        0.193494        0.224395   
1099211857         0.174663        0.139265        0.188047        0.220157   
...                     ...             ...             ...             ...   
1099211857         0.288199        0.053180        0.171834        0.253824   
1099211857         0.285221        0.059209        0.176116        0.256549   
1099211857         0.270156        0.046781        0.160500        0.242670   
1099211857         0.323372        0.090129        0.201965        0.281205   
1099211857         0.267551        0.057752        0.157425        0.228584   

             x_right_hand_8  x_right_hand_9  ...  x_right_hand_11  \
sequence_id                                  ...                    
1099211857         0.249187        0.101526  ...         0.175716   
1099211857         0.241598        0.093737  ...         0.148199   
1099211857         0.247182        0.098625  ...         0.152872   
1099211857         0.249390        0.098467  ...         0.153995   
1099211857         0.245529        0.096810  ...         0.153500   
...                     ...             ...  ...              ...   
1099211857         0.318933        0.043743  ...         0.273070   
1099211857         0.320234        0.050721  ...         0.282372   
1099211857         0.309588        0.036164  ...         0.260327   
1099211857         0.348650        0.074285  ...         0.299383   
1099211857         0.284262        0.045829  ...         0.241643   

             x_right_hand_12  x_right_hand_13  x_right_hand_14  \
sequence_id                                                      
1099211857          0.197631         0.046775         0.061516   
1099211857          0.170814         0.039341         0.053241   
1099211857          0.178564         0.045534         0.059244   
1099211857          0.176758         0.047170         0.066222   
1099211857          0.174838         0.047815         0.067358   
...                      ...              ...              ...   
1099211857          0.343791         0.052902         0.177304   
1099211857          0.349637         0.058132         0.181486   
1099211857          0.329498         0.041259         0.164009   
1099211857          0.363257         0.075061         0.194823   
1099211857          0.306652         0.044523         0.152903   

             x_right_hand_15  x_right_hand_16  x_right_hand_17  \
sequence_id                                                      
1099211857          0.072928         0.086281        -0.010396   
10

In [169]:
visualise2d_landmarks(reversed_sequence, f"Phrase: {sequence_phrase}")

In [154]:
left_data

sequence_id  frame  x_left_hand_0  x_left_hand_1  x_left_hand_2  \
12      1817221592    9.0       0.563295       0.459576       0.381724   
15      1817248431    9.0       0.680857       0.577381       0.505314   
17      1817348598    9.0       0.956424       0.889103       0.818419   
20      1817382273    9.0       0.802836       0.736705       0.673200   
25      1817651236    9.0       0.856107       0.756596       0.692620   
...            ...    ...            ...            ...            ...   
67233    386361726    9.0       0.598941       0.518246       0.480507   
67234    386466332    9.0       0.599616       0.537741       0.475229   
67267    387390786    9.0       0.585973       0.480971       0.346336   
67284    388225542    9.0       0.658460       0.576647       0.500126   
67285    388232076    9.0       0.832166       0.812121       0.697527   

       x_left_hand_3  x_left_hand_4  x_left_hand_5  x_left_hand_6  \
12          0.321069       0.285747       0.490891       0.451477   
15          0.478172       0.466133       0.570973       0.534812   
17          0.765783       0.722212       0.831799       0.755638   
20          0.646170       0.657284       0.702647       0.655930   
25          0.653095       0.628491       0.698044       0.625628   
...              ...            ...            ...            ...   
67233       0.499069       0.523064       0.554946       0.477944   
67234       0.435517       0.414458       0.547506       0.535840   
67267       0.270746       0.226656       0.408268       0.342510   
67284       0.436581       0.374855       0.554448       0.494012   
67285       0.569774       0.467846       0.735782       0.526173   

       x_left_hand_7  ...    r    s    t    u    v    w    x    y    z    ~  
12          0.401009  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
15          0.509518  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
17          0.716922  ...  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  
20          0.620662  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
25          0.603176  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
...              ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
67233       0.446889  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67234       0.498025  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67267       0.326518  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67284       0.447618  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
67285       0.400693  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[6552 rows x 187 columns]

In [12]:
reversed_left_data = left_data
for i in range(21):
    reversed_left_data['x_right_hand_'+str(i)] = left_data['x_left_hand_0'] - left_data['x_left_hand_'+str(i)]
    reversed_left_data['y_right_hand_'+str(i)] = left_data['y_left_hand_'+str(i)] - left_data['y_left_hand_0']
    reversed_left_data['z_right_hand_'+str(i)] = left_data['z_left_hand_'+str(i)] - left_data['z_left_hand_0']

/tmp/ipykernel_28/1398007537.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  reversed_left_data['x_right_hand_'+str(i)] = left_data['x_left_hand_0'] - left_data['x_left_hand_'+str(i)]
/tmp/ipykernel_28/1398007537.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  reversed_left_data['y_right_hand_'+str(i)] = left_data['y_left_hand_'+str(i)] - left_data['y_left_hand_0']
/tmp/ipykernel_28/1398007537.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using

In [13]:
reversed_left_data[x_right_hand_cols]

x_right_hand_0  x_right_hand_1  x_right_hand_2  x_right_hand_3  \
12                0.0        0.103718        0.181571        0.242225   
15                0.0        0.103477        0.175543        0.202685   
17                0.0        0.067321        0.138005        0.190641   
20                0.0        0.066130        0.129636        0.156666   
25                0.0        0.099511        0.163487        0.203012   
...               ...             ...             ...             ...   
67233             0.0        0.080695        0.118433        0.099872   
67234             0.0        0.061875        0.124387        0.164100   
67267             0.0        0.105003        0.239638        0.315228   
67284             0.0        0.081813        0.158335        0.221879   
67285             0.0        0.020045        0.134639        0.262393   

       x_right_hand_4  x_right_hand_5  x_right_hand_6  x_right_hand_7  \
12           0.277548        0.072404        0.111818        0.162286   
15           0.214724        0.109885        0.146045        0.171339   
17           0.234212        0.124624        0.200786        0.239502   
20           0.145552        0.100189        0.146906        0.182174   
25           0.227616        0.158063        0.230479        0.252931   
...               ...             ...             ...             ...   
67233        0.075876        0.043995        0.120996        0.152052   
67234        0.185158        0.052111        0.063776        0.101592   
67267        0.359318        0.177705        0.243464        0.259455   
67284        0.283605        0.104012        0.164448        0.210842   
67285        0.364320        0.096384        0.305994        0.431473   

       x_right_hand_8  x_right_hand_9  ...  x_right_hand_11  x_right_hand_12  \
12           0.201821       -0.000316  ...         0.029143         0.057745   
15           0.193187        0.046676  ...         0.033881         0.036607   
17           0.270905        0.076427  ...         0.174842         0.206910   
20           0.209636        0.032382  ...         0.062433         0.081932   
25           0.257994        0.102351  ...         0.245788         0.257870   
...               ...             ...  ...              ...              ...   
67233        0.161938       -0.016741  ...         0.086437         0.078921   
67234        0.131614        0.008178  ...         0.100414         0.118999   
67267        0.250644        0.101836  ...         0.227327         0.209226   
67284        0.257281        0.059551  ...         0.142967         0.185239   
67285        0.525940        0.117481  ...         0.494983         0.577981   

       x_right_hand_13  x_right_hand_14  x_right_hand_15  x_right_hand_16  \
12           -0.073703        -0.107484        -0.118323        -0.117913   
15           -0.011664         0.010596         0.076151         0.126692   
17            0.027791         0.064532         0.091147         0.118776   
20           -0.034371        -0.001333         0.030509         0.050662   
25            0.047506         0.165721         0.181709         0.176223   
...                ...              ...              ...              ...   
67233        -0.072680         0.023069         0.027397         0.021195   
67234        -0.037851         0.022191         0.080085         0.093142   
67267         0.017200         0.115865         0.151215         0.137755   
67284         0.010960         0.026812         0.067603         0.109350   
67285         0.150950         0.371869         0.365447         0.314783   

       x_right_hand_17  x_right_hand_18  x_right_hand_19  x_right_hand_20  
12           -0.135531        -0.199326        -0.239979        -0.271669  
15           -0.063428        -0.013939         0.046665         0.095063  
17           -0.017449        -0.002238         0.011359         0.029574  
20           -0.093681        -0.050323        -0.009264       

In [14]:
centered_right_data = right_data
for i in range(21):
    centered_right_data['x_right_hand_'+str(i)] = right_data['x_right_hand_'+str(i)] - right_data['x_right_hand_0']
    centered_right_data['y_right_hand_'+str(i)] = right_data['y_right_hand_'+str(i)] - right_data['y_right_hand_0']
    centered_right_data['z_right_hand_'+str(i)] = right_data['z_right_hand_'+str(i)] - right_data['z_right_hand_0']

/tmp/ipykernel_28/2182201144.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  centered_right_data['x_right_hand_'+str(i)] = right_data['x_right_hand_'+str(i)] - right_data['x_right_hand_0']
/tmp/ipykernel_28/2182201144.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  centered_right_data['y_right_hand_'+str(i)] = right_data['y_right_hand_'+str(i)] - right_data['y_right_hand_0']
/tmp/ipykernel_28/2182201144.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.

In [15]:
centered_right_data[x_right_hand_cols]

x_right_hand_0  x_right_hand_1  x_right_hand_2  x_right_hand_3  \
2                 0.0        0.309877        0.393591        0.435680   
3                 0.0        0.283690        0.326063        0.390095   
4                 0.0        0.360817        0.435711        0.471842   
5                 0.0        0.378974        0.462083        0.523368   
6                 0.0        0.397529        0.451431        0.481075   
...               ...             ...             ...             ...   
67278             0.0        0.445246        0.489773        0.503756   
67279             0.0        0.345800        0.468640        0.511581   
67280             0.0        0.318508        0.362608        0.380038   
67281             0.0        0.497081        0.594043        0.656642   
67282             0.0        0.392563        0.448451        0.472186   

       x_right_hand_4  x_right_hand_5  x_right_hand_6  x_right_hand_7  \
2            0.415816        0.363555        0.400078        0.400655   
3            0.444488        0.340134        0.435782        0.490321   
4            0.446278        0.368748        0.399602        0.426213   
5            0.583684        0.382783        0.396603        0.421799   
6            0.491940        0.402531        0.426195        0.452468   
...               ...             ...             ...             ...   
67278        0.476808        0.429719        0.421298        0.413083   
67279        0.500202        0.421248        0.462495        0.489689   
67280        0.378171        0.371188        0.417413        0.447705   
67281        0.730945        0.517775        0.568383        0.597423   
67282        0.457346        0.405689        0.463841        0.511855   

       x_right_hand_8  x_right_hand_9  ...  x_right_hand_11  x_right_hand_12  \
2            0.386491        0.300033  ...         0.335020         0.326310   
3            0.534337        0.377112  ...         0.538801         0.584996   
4            0.440698        0.302883  ...         0.389386         0.370915   
5            0.451607        0.314697  ...         0.384653         0.431699   
6            0.482349        0.342585  ...         0.362772         0.388984   
...               ...             ...  ...              ...              ...   
67278        0.408127        0.386491  ...         0.340654         0.333216   
67279        0.496687        0.351551  ...         0.407519         0.388646   
67280        0.480022        0.319795  ...         0.354840         0.379851   
67281        0.620599        0.431678  ...         0.475023         0.489528   
67282        0.557659        0.343636  ...         0.404927         0.444171   

       x_right_hand_13  x_right_hand_14  x_right_hand_15  x_right_hand_16  \
2             0.230608         0.258482         0.277284         0.276473   
3             0.412398         0.506827         0.479618         0.445177   
4             0.237707         0.307410         0.335657         0.318365   
5             0.240256         0.249956         0.291507         0.345212   
6             0.289915         0.274864         0.286804         0.311034   
...                ...              ...              ...              ...   
67278         0.344437         0.345049         0.385208         0.419921   
67279         0.269680         0.335357         0.331568         0.309074   
67280         0.264103         0.262897         0.281767         0.302441   
67281         0.351693         0.342292         0.333559         0.330922   
67282         0.290835         0.336311         0.393125         0.443021   

       x_right_hand_17  x_right_hand_18  x_right_hand_19  x_right_hand_20  
2             0.157418         0.185557         0.214169         0.222341  
3             0.442915         0.513140         0.489857         0.459495  
4             0.165949         0.239659         0.273471         0.262015  
5             0.164809         0.097263         0.059628       

In [18]:
x_right_hand_cols_1 = sign.columns[np.arange(524,544)]
y_right_hand_cols_1 = sign.columns[np.arange(1067,1087)]
z_right_hand_cols_1 = sign.columns[np.arange(1610, 1630)]

In [21]:
z_right_hand_cols_1

Index(['z_right_hand_1', 'z_right_hand_2', 'z_right_hand_3', 'z_right_hand_4',
       'z_right_hand_5', 'z_right_hand_6', 'z_right_hand_7', 'z_right_hand_8',
       'z_right_hand_9', 'z_right_hand_10', 'z_right_hand_11',
       'z_right_hand_12', 'z_right_hand_13', 'z_right_hand_14',
       'z_right_hand_15', 'z_right_hand_16', 'z_right_hand_17',
       'z_right_hand_18', 'z_right_hand_19', 'z_right_hand_20'],
      dtype='object')

In [22]:
right_hand_cols = np.concatenate((x_right_hand_cols_1, y_right_hand_cols_1, z_right_hand_cols_1))

In [23]:
right_hand_cols

array(['x_right_hand_1', 'x_right_hand_2', 'x_right_hand_3',
       'x_right_hand_4', 'x_right_hand_5', 'x_right_hand_6',
       'x_right_hand_7', 'x_right_hand_8', 'x_right_hand_9',
       'x_right_hand_10', 'x_right_hand_11', 'x_right_hand_12',
       'x_right_hand_13', 'x_right_hand_14', 'x_right_hand_15',
       'x_right_hand_16', 'x_right_hand_17', 'x_right_hand_18',
       'x_right_hand_19', 'x_right_hand_20', 'y_right_hand_1',
       'y_right_hand_2', 'y_right_hand_3', 'y_right_hand_4',
       'y_right_hand_5', 'y_right_hand_6', 'y_right_hand_7',
       'y_right_hand_8', 'y_right_hand_9', 'y_right_hand_10',
       'y_right_hand_11', 'y_right_hand_12', 'y_right_hand_13',
       'y_right_hand_14', 'y_right_hand_15', 'y_right_hand_16',
       'y_right_hand_17', 'y_right_hand_18', 'y_right_hand_19',
       'y_right_hand_20', 'z_right_hand_1', 'z_right_hand_2',
       'z_right_hand_3', 'z_right_hand_4', 'z_right_hand_5',
       'z_right_hand_6', 'z_right_hand_7', 'z_right_hand_8',
  

In [30]:
clean_data = pd.concat([centered_right_data[right_hand_cols],reversed_left_data[right_hand_cols]], axis = 0)

In [31]:
clean_data.to_csv('clean_features')

In [38]:
data.index

RangeIndex(start=0, stop=67288, step=1)

In [39]:
clean_data.index

Int64Index([    2,     3,     4,     5,     6,     7,     8,     9,    14,
               16,
            ...
            67159, 67163, 67184, 67192, 67226, 67233, 67234, 67267, 67284,
            67285],
           dtype='int64', length=38578)

In [42]:
clean_labels = data.loc[clean_data.index].iloc[:,-59:]

In [43]:
clean_labels.to_csv('clean_labels')